In [1]:
# Useful for defining quantities
from astropy import units as u
from astropy.coordinates import cartesian_to_spherical

# Earth focused modules, ISS example orbit and time span generator
from poliastro.earth import EarthSatellite
from poliastro.earth.plotting import GroundtrackPlotter
from poliastro.twobody import Orbit
from poliastro.spacecraft import Spacecraft
from poliastro.examples import iss
from poliastro.util import time_range
from poliastro.bodies import Earth

In [2]:
import numpy as np
import matplotlib.pyplot as plt
from scipy import interpolate

In [3]:
from ipywidgets import interact, interactive, fixed, interact_manual, FloatSlider, IntSlider
import ipywidgets as widgets

In [4]:
radius_E = 6400

In [17]:
store = lambda: None
store.satelites = []

$e=0$ (eccentricity)   
$a=18 261.8$ km (radius)  
$i=80^\circ$ (inclination)  
$\Omega = 0^\circ$ - arbitrary (longitude of ascending node)  
$\omega_1 = 0^\circ$ $\omega_2 = 60^\circ$  (argument of periapsis)  
$\delta\theta=20^\circ$ (true anomaly __spacing__)   
$T=6.838$ h  
$T_{rep} = 6$ days  

In [25]:
@interact(h=FloatSlider(min=7000, max=19000,value=11700, step=100, continuous_update=False),
          i=FloatSlider(min=0, max=90, step=1,value=80, continuous_update=False),
          duration=IntSlider(min=20, max=300, step=10,value=48, continuous_update=False),
          max_day_bn_rep=IntSlider(value=6,min=1, max=30, step=1, continuous_update=False))
def groundtract(h, i, duration,max_day_bn_rep):
    # Build spacecraft instance
    a = (radius_E+h) * u.km
    ecc = 0 * u.one
    inc = i * u.deg
    raan = 0 * u.deg
    argp = 0 * u.deg
    nu = 0 * u.deg
    orb = Orbit.from_classical(Earth, a, ecc, inc, raan, argp, nu)
    print("Original period: ", orb.period.to(u.h))
    #adjust to integer orbits in a day
    T_E =  Earth.rotational_period.to(u.s)
    ratio =T_E/orb.period 
    ratio = np.floor(max_day_bn_rep*ratio)/float(max_day_bn_rep)*u.one
    new_period = T_E/ratio
    a = (Earth.k*(new_period/2/np.pi)**2)**(1./3)
    orb = Orbit.from_classical(Earth, a, ecc, inc, raan, argp, nu)

    print("Adjusted period: ", orb.period.to(u.h), "Adjusted altitude: ", (a - radius_E*u.km).to(u.km))
    sat = EarthSatellite(orb, None)
    t_span = time_range(orb.epoch, periods=5*duration, end= orb.epoch + duration*u.h)
    gp = GroundtrackPlotter()
    gp.update_layout(title="Groundtrack")

    # Plot previously defined EarthSatellite object
    gp.plot(
        sat,
        t_span,
        label="Sat",
        color = "red",
    )
    store.gp_groundtract = gp
    store.sat = sat
    store.t_span = t_span
    store.t_end = duration*u.h
    gp.fig.show()

interactive(children=(FloatSlider(value=11700.0, continuous_update=False, description='h', max=19000.0, min=70…

In [7]:
#store.gp_groundtract.update_geos(projection_type="orthographic")


In [51]:
@interact(ground_size=FloatSlider(min=0,max=30,value=20,continuous_update=False),
          n_sats = IntSlider(min=6,max=3600,value=18, continuous_update=False))
def groundshadow(ground_size, n_sats):
    # ground_size in degrees is the size of a tile on the surface
    # n_sats is the number of satelites on one repetion of an orbit
    # for heights > continuous coverage height, n_sats * grounds_size can be = 350
    # below continous coverage height, more n_sats are needed
    data = store.gp_groundtract.fig.data[1]
    ts = store.t_span-store.sat.orbit.epoch
    lats = interpolate.interp1d(ts.to(u.h), data['lat'],fill_value='extrapolate')
    lons = interpolate.interp1d(ts.to(u.h), data['lon'],fill_value='extrapolate')
    delta_omega = store.sat.orbit.period.to(u.h)*(25/360)
    store.satelites = lambda: None
    store.satelites.lat = []
    store.satelites.lon = []
    store.centers = lambda: None
    store.centers.lat = []
    store.centers.lon = []
    theta = np.linspace(2*np.pi,0)
    dt = store.sat.orbit.period.to(u.h)/n_sats
    t0 = ts[0].to(u.h)
    tend = ts[-1].to(u.h)
    for t in np.linspace(t0,tend,int(tend/dt)):
        store.gp_groundtract.fig.add_scattergeo(mode='text',fill='toself',fillcolor='blue', 
                      lat=lats(t)+ground_size/2*np.sin(theta),
                      lon=lons(t)+ground_size/2*np.cos(theta),
                                                opacity=0.3)
        #store.gp_groundtract.fig.add_scattergeo(lat=lats(t-delta_omega), lon=lons(t-delta_omega),marker={"size": 20, "symbol": "triangle-right",'color':'black'})
        store.satelites.lat.append(lats(t-delta_omega))
        store.satelites.lon.append(lons(t-delta_omega))
        store.centers.lat.append(lats(t))
        store.centers.lon.append(lons(t))
    store.gp_groundtract.update_geos()
    store.gp_groundtract.fig.show()

interactive(children=(FloatSlider(value=20.0, continuous_update=False, description='ground_size', max=30.0), I…

In [53]:
np.savetxt('cache/tiles1_lon.csv',np.array(store.centers.lon))

In [39]:
groundtract(11700, 80, 48,6)
groundshadow(20, 18)

Original period:  6.7317246260881 h
Adjusted period:  6.838421485714274 h Adjusted altitude:  11890.75321705091 km


In [54]:
# Build spacecraft instance
h, i, duration, max_day_bn_rep = 11700, 80, 48, 6
a = (radius_E+h) * u.km
ecc = 0 * u.one
inc = i * u.deg
raan = 0 * u.deg
argp = 60 * u.deg
nu = 0 * u.deg
orb = Orbit.from_classical(Earth, a, ecc, inc, raan, argp, nu)
print("Original period: ", orb.period.to(u.h))
#adjust to integer orbits in a day
T_E =  Earth.rotational_period.to(u.s)
ratio =T_E/orb.period 
ratio = np.floor(max_day_bn_rep*ratio)/float(max_day_bn_rep)*u.one
new_period = T_E/ratio
a = (Earth.k*(new_period/2/np.pi)**2)**(1./3)
orb = Orbit.from_classical(Earth, a, ecc, inc, raan, argp, nu)

print("Adjusted period: ", orb.period.to(u.h), "Adjusted altitude: ", (a - radius_E*u.km).to(u.km))
sat = EarthSatellite(orb, None)
t_span = time_range(orb.epoch, periods=5*duration, end= orb.epoch + duration*u.h)
gp = store.gp_groundtract
gp.update_layout(title="Groundtrack")

# Plot previously defined EarthSatellite object
gp.plot(
    sat,
    t_span,
    label="omega=60",
    color = "blue",
)
store.gp_groundtract = gp
store.sat = sat
store.t_span = t_span
store.t_end = duration*u.h
gp.fig.show()

Original period:  6.7317246260881 h
Adjusted period:  6.838421485714274 h Adjusted altitude:  11890.75321705091 km


In [16]:
gp.fig.show()

In [55]:
ground_size, n_sats = 20, 18

data = store.gp_groundtract.fig.data[-2]
ts = store.t_span-store.sat.orbit.epoch
lats = interpolate.interp1d(ts.to(u.h), data['lat'],fill_value='extrapolate')
lons = interpolate.interp1d(ts.to(u.h), data['lon'],fill_value='extrapolate')
theta = np.linspace(2*np.pi,0)
dt = store.sat.orbit.period.to(u.h)/n_sats
t0 = ts[0].to(u.h)
tend = ts[-1].to(u.h)
store.satelites2 = lambda: None
store.satelites2.lat = []
store.satelites2.lon = []
store.centers2 = lambda: None
store.centers2.lat = []
store.centers2.lon = []
delta_omega = store.sat.orbit.period.to(u.h)*(25/360)

for t in np.linspace(t0,tend,int(tend/dt)):
    store.gp_groundtract.fig.add_scattergeo(mode='text',fill='toself',fillcolor='red', 
                  lat=lats(t)+ground_size/2*np.sin(theta),
                  lon=lons(t)+ground_size/2*np.cos(theta),
                                            opacity=0.3)
    store.satelites2.lat.append(lats(t-delta_omega))
    store.satelites2.lon.append(lons(t-delta_omega))
    store.centers2.lat.append(lats(t))
    store.centers2.lon.append(lons(t))
store.gp_groundtract.update_geos()
store.gp_groundtract.fig.show()

In [57]:
np.savetxt('cache/tiles2_lat.csv',np.array(store.centers2.lat))

In [33]:
gp.update_geos(projection_type="orthographic")

In [47]:
points1 = store.gp_groundtract.fig.data[1]
points2 = store.gp_groundtract.fig.data[129]

In [50]:
len(points1['lat'])

240

In [279]:
np.savetxt(f'cache/actually_looks_good_2src.csv',
            np.vstack([
                np.vstack([points1['lat'],points1['lon']]).T, 
                np.vstack([points2['lat'],points2['lon']]).T]),
                delimiter=',')